In [ ]:
##Python venv: search_agent_poc

In [2]:
##This module will take the serialized dictionary got out of PDF Parsing ann try to extract
##Semantic Knowldge like identifying 
## 1.Important Objects/Entities
## 2.Deduplicate Entities
## 3.Extracting Relations
## 4.Extract the main Ideas/Topics around Each Page
## 5.Link the different topics via diffrent entities/Objects
## 6.Break down the document by pages instead of Chunks .
## 7.If a page does not fit a chunk then chunk them extract information and then deduplicate the information across
## the page.

#Next Steps:
## 5.Try to Seggregate the BigPDF on Sections.
## 8.Try To Find Common Objects or ideas that link these sections.
## 9.Try 

In [41]:
import numpy as np
import numpy as np
import matplotlib.pyplot as plt
import os
import json
import pickle
import ollama
import chromadb
from chromadb.config import DEFAULT_TENANT, DEFAULT_DATABASE, Settings


import pandas as pd
#from langchain_community.vectorstores import Chroma

In [42]:
import pickle
import pandas as pd
#rag_test_input_path='/home/matrix4284/MY_GEN_AI_PROJECTS/RAG/GraphRAG/graphrag-local-ollama/ragtest/input/'+file_name
import os
# importing shutil module
import shutil

from langchain_community.chat_models import ChatOllama

from langchain_community.embeddings import HuggingFaceEmbeddings

from langchain_community.embeddings.sentence_transformer import (
    SentenceTransformerEmbeddings,
)

#from sentence_transformers import SentenceTransformer
#embeddings = SentenceTransformer("all-MiniLM-L6-v2")

from langchain.text_splitter import RecursiveCharacterTextSplitter
from langchain_community.vectorstores import Chroma

import json
import operator
from typing import Annotated, Sequence, TypedDict

from langchain import hub
from langchain.prompts import PromptTemplate
from langchain_community.vectorstores import Chroma
from langchain_core.messages import BaseMessage, FunctionMessage
from langchain_core.output_parsers import StrOutputParser
from langchain_core.pydantic_v1 import BaseModel, Field
from langchain_core.runnables import RunnablePassthrough
from langchain_community.chat_models import ChatOllama
from langchain_core.output_parsers import JsonOutputParser
import json
import operator
from typing import Annotated, Sequence, TypedDict

from langchain import hub
from langchain.prompts import PromptTemplate
from langchain_community.vectorstores import Chroma
from langchain_core.messages import BaseMessage, FunctionMessage
from langchain_core.output_parsers import StrOutputParser
from langchain_core.pydantic_v1 import BaseModel, Field
from langchain_core.runnables import RunnablePassthrough
from langchain_community.chat_models import ChatOllama
from langchain_core.output_parsers import JsonOutputParser
from langchain_core.output_parsers import StrOutputParser
from langchain.output_parsers import XMLOutputParser

In [43]:
import networkx as nx
from pyvis.network import Network

In [44]:
graph_output_dir="./graph_output_networkx/"
single_entity_file="nodes_with_single_ocurence.csv"
input_graph="graph_phase2_with_single_entity_desc_embeddings.graphml"
output_graph_graphml="graph_phase3_with_multi_occurence_nodes_entity_desc_embeddings.graphml"
output_graph_gml="graph_phase3_with_multi_occurence_nodes_entity_desc_embeddings.gml"
pdf_enrichment_output_dir = '../pdf_enrichment/pdf_enriched_output/'  
pdf_enrichment_output_file = 'pdf_enriched_content_dict_phase5_extract_highligts_478_final.pickle'


client = chromadb.PersistentClient(
    path="./Kubernetes_in_Action_ChromaDB",
    settings=Settings(),
    tenant=DEFAULT_TENANT,
    database=DEFAULT_DATABASE,
)


In [45]:
graph_output_dir='./graph_output_networkx/'
multi_entity_file='nodes_with_multi_ocurence.csv'
multi_df=pd.read_csv(graph_output_dir+multi_entity_file)
multi_df=multi_df.reset_index(drop=True).reset_index().dropna()
multi_df['index']

0          0
1          1
2          2
3          3
4          4
        ... 
4346    4346
4347    4347
4348    4348
4349    4349
4350    4350
Name: index, Length: 4340, dtype: int64

In [40]:
#### Normalizing the Description for each entity as the same entity appearing in different context or relations####
#### or references may be slighly diffrent description according to the context#####
####Our idea is to group the data frame by 'entity' and get the array of desription for its each context####
####Then after aggrgrating the description from each context or relations we summatrize in in a fluent & informative###
####Description using llama-3.1

In [8]:
model_name="llama3.1"
book_text=''
page_text=''
file_name='Kubernetes_in_action_text_only'
extension='.txt'
start_page_idx=0
end_page_index=479
#full_filename=file_name+'_'+str(page_idx)+extension
#full_filename
pdf_enrichment_output_dir='../pdf_enrichment/pdf_enriched_output/'

#LLM Model for Prompt Tuning
llm = ChatOllama(base_url="http://192.168.50.100:11434",model=model_name,temperature=0.15)

In [9]:


####Function to aggregrate all the descritption found for a node for different references.#####
def desc_aggr_str(desc_lst):
    desc_str=""
    for desc in desc_lst:
        #print(desc)
        desc_str=desc_str+desc
        #print(desc)
    return desc_str

# Function to reverse a string
def reverse(string):
    string = string[::-1]
    return string

####This function summarizes the aggregated descritption found for the same entity but in different different context#######
#### or relations or references###
####We are using llama-3.1 to summarize the aggrgated entities into a fluent and informative summary#####
def description_normalizer(raw_description):
    
    prompt = PromptTemplate(
            template="""You are a computer technology expert who has mastery in Kubernetes,Docker,\n
            Machine Learning,Generative AI,Natural Language Understanding and Computer Vision.\n
            You are also extremely good at writing precise content given several contents for related things\n
            You have to deeply study a raw description which has been jotted down from several sources.  \n
            You have to study the jotted down description and re-write in a way so that it conveys the meaning\n
            that was intended by the jotten down description.\n
            You should make up any new information on your own hence the information content in your output \n
            should match the raw description information. \n
            There is no need to mention any header statement before the summary.\n
            Wrap the summary in a json with key named summary.\n
            Output the json and nothing else no headers no footers.\n
            Here is the raw description: \n\n {context} \n\n""",
            input_variables=["context"],
            ###Introduced by Kaustav while experimenting with XMLParsers
            #partial_variables={"format_instructions": parser.get_format_instructions()},
    )

    # Chain
    #Commented out By Kaustav 20/08/2024 as str output parser is giving some unwanted text #####
    chain = prompt | llm | StrOutputParser()
    
    output = chain.invoke(
        {
                "context": raw_description,
        }
    )
    
    json_output=output
    
    #print("Formatted Output:")
    #print(json_output)
    
    
    if '[' in json_output:
        json_output=json_output.split('[')[1]
        json_output='['+json_output
    elif '{' in json_output:
        json_output=json_output.split('{')[1]
        json_output='{'+json_output
        json_output='['+json_output
            
        #page_output_json=json.loads(output)
        
    
        #print('JSON OUTPUT:')
    #print(json_output)
        #except:
        #    json_output=json_output
        #    cotinue
        
        #try:
    if ']' in json_output:
        json_output=reverse(json_output)
        #print('Reversed JSON OUTPUT:')
        #print(json_output)
        json_output=json_output.split(']')[1]
        json_output=reverse(json_output)
        #json_output=json_output.rsplit(']')[-1]
        #page_output_json=json.loads(output)
        #print('JSON OUTPUT:')
        #print(json_output)
        json_output= json_output + ']'
        #print('JSON OUTPUT:')
        #print(json_output) 
    elif '}' in json_output:
        json_output=json_output.split('}')[0]
        json_output=json_output+'}'
        json_output=json_output+']'
    
    try:
        json_output=json.loads(json_output)
        formatted_description=json_output[0]['summary']
        print("Formatted Description:")
        print(formatted_description)
        return formatted_description
    except:
        print("Cannot load json for this raw description:"+str(json_output))
        return "Cannot load json for this raw description:"+str(json_output)
    
#entity_idx=0
def embedder(index,text,collection):
    print(text)
    response = ollama.embeddings(model="mxbai-embed-large", prompt=text)
    embedding = response["embedding"]
    #print(np.array(embedding))
    try:
        collection.add(
            ids=[str(index)],
            embeddings=[embedding],
            documents=[text]
          )
    except:
          'COULD NOT LOAD INTO VECTOR DATABASE'
    #entity_idx=entity_idx+1
    return embedding

def multi_ref_entity_category_extractor(entity,description):
    prompt = PromptTemplate(
            template="""You are a computer technology expert who has mastery in Kubernetes,Docker\n
            Machine Larning,Generative AI,Natural Language Understanding and Computer Vision.\n
            The entities  are provided as input along with the description for the entities.\n
            By using the entity name and description provided you have to map the entities to a single category\n
            The category name can be like \n
            hardware,software,network,application,database,process,thread,container etc.\n
            you must select only one category per entity.The number of category per entity should only be 1.\n
            After extracting all the entities along with their category format as per rules below: \n
            1.For each entity create a json with 1 keys "category". \n
            2.Each extracted category must be enlosed within double quotes. \n
            Do not output anything other than the json neither heading/decsription before the list of json\n
            nor any decsription/footer below the json \n
            Here is the entity: \n\n {entity} \n\n and the description of the entity: \n\n {description} \n\n""",
            input_variables=["entity","description"],
            #partial_variables={"format_instructions": parser.get_format_instructions()},
    )

    # Chain
    #Commented out By Kaustav 20/08/2024 as str output parser is giving some unwanted text #####
    chain = prompt | llm | StrOutputParser()
   
    




    #Trying out XML Output parser by Kautsva added 20/08/2024####
    #chain = prompt | llm | parser
    
    

    # Score
    #filtered_docs = []
    
    #print("Page Text")
    #print(page_text)

    output = chain.invoke(
        {
                "entity": entity,
                "description":description
        }
    )
    
    #print('Relationship Output from LLM"')
    #print(output)
    
    json_output=output
    
    if '[' in json_output:
        json_output=output.split('[')[1]
        json_output='['+json_output
    else:    
        json_output='['+json_output
    
    #print('JSON OUTPUT:')
    #print(json_output)
    
    

    json_output=reverse(json_output)
    
    if ']' in json_output:
        json_output=json_output.split(']')[1]
        json_output=reverse(json_output)
        json_output= json_output + ']'
    else:
        json_output=reverse(json_output)
        json_output= json_output + ']'
    
    
    try:
        category_json=json.loads(json_output)
        print("Category Output:")
        category=category_json[0]['category']
        print(category)
        return category
    except:
        print("Category could not be parsed due to corrupt format and doc")
        return "Not Available"
    #category=category_json[0]['category']
    
    return category


def multi_ref_node_builder(entity,description,category):
    G.add_node(entity, label=entity , title=entity , description=description, category=category ,color="cyan")
    
#####Linking Single Occurence entities to pages ##########
def link_multi_ref_entities_with_page(G,document_dict_deserialized):
    doc_len=len(document_dict_deserialized)
    for page_idx in range(0,doc_len):
    
        #Adding the Page Number Nodes and connecting then to the root Node that is the document_name name node
        #Form the page number from the dictionary metadata 'page'
        entity_list=document_dict_deserialized[page_idx]['entities']
        page_num="Page_"+ str(document_dict_deserialized[page_idx]['page'])
        #G.add_node(page_idx, label=page_num , title=page_num,color="blue")
        #G.add_edge(1,page_idx)
    
        ##Under each Page we will add the different types of extracted entities like tables,text,images
        #We will Create and add the text node and attach it with the page_num node.
        #text_idx='text_'+str(i)
        #G.add_node(text_idx, label=document_dict_deserialized[i]['text'] , title=document_dict_deserialized[i]['text'],color="violet")
        #G.add_edge(page_idx,text_idx)
        #print(page_num)
        #print(document_dict_deserialized[page_idx]['entities'])
    
    
    
        
    
        for entity in multi_ref_entity_lst:
            print('Entity:')
            print(entity)
            if entity in G.nodes:
                G.add_edge(page_idx,entity,name='contains')
            else:
                print("The Entity is a kind of entity which has occured multiple times ,hence will be handled later ")
    #entities_list_doc.extend(document_dict_deserialized[i]['entities'])
    return G

#entity_idx=0
def embedder(index,text,collection):
    print(text)
    response = ollama.embeddings(model="mxbai-embed-large", prompt=text)
    embedding = response["embedding"]
    #print(np.array(embedding))
    try:
        collection.add(
            ids=[str(index)],
            embeddings=[embedding],
            documents=[text]
          )
    except:
          'COULD NOT LOAD INTO VECTOR DATABASE'
    #entity_idx=entity_idx+1
    return embedding

index            entity  \
0         0            Docker   
1         1        Kubernetes   
2         2              Pods   
3         3        Containers   
4         4  Linux namespaces   
...     ...               ...   
4346   4346            server   
4347   4347              name   
4348   4348          minikube   
4349   4349           cluster   
4350   4350         namespace   

                                            description     category  \
0                             Containerization platform     software   
1                        Container orchestration system     software   
2     Group of containers that share resources and r...  application   
3          Isolated execution environment for processes    container   
4                 Resource isolation mechanism in Linux      process   
...                                                 ...          ...   
4346  field in the cluster definition that specifies...      network   
4347  field in the context definition that specifies...     database   
4348             name of the kubectl context being used  application   
4349  field in the context definition that specifies...     database   
4350  field in the context definition that specifies...  application   

     node_occurence_flag  
0                  Multi  
1                  Multi  
2                  Multi  
3                  Multi  
4                  Multi  
...                  ...  
4346               Multi  
4347               Multi  
4348               Multi  
4349               Multi  
4350               Multi  

[4340 rows x 5 columns]

In [11]:
###the data frame of Entity which have got multiple references.
entity_multi_node_desc_df=multi_df_final.groupby(['entity'])['description'].aggregate(lambda x: list(x))
entity_multi_node_desc_df=entity_multi_node_desc_df.reset_index()




In [12]:
len(entity_multi_node_desc_df)

747

In [13]:
#### the column 'description_raw_str' contains the aggrgated description for the same entity but referenced##
#### in diffrent relations######

entity_multi_node_desc_df['description_raw_str']=entity_multi_node_desc_df['description'].apply(lambda x: desc_aggr_str(x))


In [14]:
####The 'description_formatted' column contains the summarized aggregrated decsription for each entity###
####Occuring in different context or relations or references#####
entity_multi_node_desc_df['description_formatted']=entity_multi_node_desc_df['description_raw_str'].apply(lambda x: description_normalizer(x))

Formatted Description:
The `kubectl get pods` command is a powerful tool in Kubernetes that allows users to retrieve detailed information about running pods within their cluster. This command provides a comprehensive view of all pods, including their status, labels, and other relevant metadata. By executing this command, users can gain insights into the current state of their pod deployments, facilitating efficient management and troubleshooting of their containerized applications.
Formatted Description:
The `delete` option allows for the removal of all resources of a specific type, such as deleting all ReplicationControllers and associated pods. This feature enables users to completely purge a particular resource type from their Kubernetes cluster, effectively resetting it to a clean state.
Formatted Description:
Kubernetes provides an option to list resources across all namespaces, enabling administrators to view and manage resources from a unified perspective. This feature allows fo

Formatted Description:
Kubernetes API objects refer to the resources managed by the Kubernetes API server, such as pods and services. These software components interact with the Kubernetes API server to manage and scale applications. Additionally, Kubernetes API objects include pod and one or more PersistentVolumeClaims referenced by the pod, created when scaling up a StatefulSet. The Replication Manager watches these objects, ensuring that the desired number of replicas is maintained. Furthermore, custom API objects can be created for Kubernetes, allowing for customizable data structures to be used within the platform. These custom objects are managed by the Kubernetes API server and provide a flexible way to extend the functionality of the system.
Formatted Description:
The Kubernetes API server, also known as the central component of the Kubernetes control plane, is a stateless server that provides a RESTful interface to interact with the cluster. It exposes the Kubernetes API and s

Formatted Description:
The Container Network Interface (CNI) plugin for Kubernetes is a software component that enables network connectivity between containers running on a cluster managed by Kubernetes. This plugin provides a standardized interface to manage container networking, allowing multiple CNI plugins to coexist and interoperate within the same Kubernetes environment. By leveraging the CNI plugin, Kubernetes can automatically configure and manage network settings for containers as they are created or deleted, ensuring seamless communication between them. The CNI plugin also supports features such as IP address management, routing, and network policy enforcement, making it an essential component in building scalable and secure containerized applications.
Formatted Description:
A Kubernetes environment variable, CPU_REQUEST, represents the CPU request for a container, measured in millicores. This variable allows users to specify the desired CPU allocation for their containers, e

Formatted Description:
A ClusterRoleBinding in Kubernetes is a cluster-level resource that binds a ClusterRole to a user, service account, or group. It grants access to resources across all namespaces, allowing users or groups to perform actions on cluster-level resources using the permissions defined in the associated ClusterRole. This binding can be used to grant permissions to users or groups across multiple namespaces, making it a powerful tool for managing access and permissions within a Kubernetes cluster.
Formatted Description:
A ClusterRoleBinding is a Kubernetes resource that establishes a binding between a ClusterRole and one or more subjects within a cluster. This binding grants the permissions defined by the ClusterRole to the bound subjects, allowing them to access resources across all namespaces in the cluster. A ClusterRoleBinding can be used to bind a ClusterRole with cluster-level permissions to specific users, groups, or ServiceAccounts, providing a way to manage and 

Formatted Description:
A pod status in Kubernetes, denoted as 'CrashLoopBackOff', signifies that a container within the pod is experiencing an infinite restart cycle due to continuous crashes. This occurs when a container's application or process fails repeatedly, causing the pod to restart with exponentially increasing delays. The CrashLoopBackOff status indicates that the container has crashed and will be restarted by Kubernetes, but it continues to experience failures, resulting in an endless loop of restarts.
Formatted Description:
A Kubernetes resource, known as a CronJob, automates the creation of Job objects at predetermined intervals, allowing for the scheduled execution of tasks that require repeated runs over time. This resource is particularly useful for pods that necessitate the utilization of Jobs or CronJobs, enabling the efficient management and orchestration of such workloads.
Formatted Description:
A Kubernetes Job object, also known as a CronJob, serves as a scheduler

...

Formatted Description:
A key security component in Kubernetes, Role-Based Access Control (RBAC) enables administrators to create and enforce fine-grained access control policies. By defining roles and assigning permissions to users or groups within the cluster, RBAC ensures that only authorized entities can interact with sensitive resources. This feature empowers administrators to manage access to a Kubernetes cluster based on predefined roles, thereby maintaining the integrity and security of the entire system. Additionally, RBAC supports nested roles, allowing for more complex permission structures to be defined. Furthermore, it integrates seamlessly with other Kubernetes features, such as namespaces and service accounts, to provide a robust and scalable access control mechanism.
Formatted Description:
Kubernetes commands, such as `kubectl rollout`, enable automatic rolling updates of ReplicationControllers and ReplicaSets by incrementally replacing old pods with new ones, ensuring m

Formatted Description:
The Network File System (NFS) server field in a Kubernetes cluster configuration defines the IP address or hostname of the NFS server that provides shared file access to pods within the cluster. This field is crucial for enabling persistent storage and data sharing across multiple containers, allowing them to access and share files as if they were on a local filesystem.
Formatted Description:
A service in Kubernetes is an abstracted interface to access resources such as pods or deployments, providing a stable network identity and load balancing. It acts as an abstraction layer that defines a set of pods, offering load balancing, self-healing, and scaling capabilities. A service can be thought of as a network identity for accessing applications within a cluster, similar to how a domain name provides access to a website. In the context of the external-service example, it represents a service that accepts incoming connections on port 80, allowing clients to communic

Formatted Description:
A YAML configuration file that defines a custom storage class, specifically designed for use within Minikube environments. This file serves as a blueprint for managing and provisioning storage resources in Kubernetes clusters running on Minikube.
Formatted Description:
The `updateStrategy` field in a Kubernetes Deployment YAML file determines how pods are updated during a rollout. It can be set to either `RollingUpdate`, which allows for incremental updates, or `Recreate`, which replaces all existing pods at once.
Formatted Description:
The "fsGroup" property allows you to specify a list of additional group IDs that a user is associated with, enabling containers to run with specific supplemental group permissions. This feature is particularly useful when defining constraints in a PodSecurityPolicy resource, where it helps enforce rules for supplemental groups.
Formatted Description:
In Kubernetes, a mechanism exists to restrict pod deployments on specific nodes. 

Formatted Description:
A semantic identifier, known as a Docker image version tag, serves as a unique marker for each iteration of an application's deployment. This tag signifies a distinct revision of the software, allowing for precise tracking and management of updates. In the context of Node.js, a newer version of the official image would introduce enhancements, bug fixes, or new features, ensuring improved performance, security, and compatibility with evolving requirements.
Formatted Description:
In Kubernetes, the `env` key within the `list` configuration is utilized to define the value of an environment variable. This field serves as a means to establish a predetermined value for an environment variable, allowing for consistent and controlled deployment settings across containers.
Formatted Description:
A configuration parameter that enables the injection of ConfigMap data into application containers as environment variables, allowing for dynamic and flexible management of enviro

Formatted Description:
A virtual region within Google Cloud Platform (GCP) where cloud resources, such as Compute Engine instances and Persistent Volumes, are hosted. This zone serves as a logical grouping of physical resources, ensuring high availability and scalability for deployed applications. The Persistent Volume, in particular, will be created within this designated zone, allowing for efficient storage and management of data.


In [15]:
entity_multi_node_desc_df['category']=entity_multi_node_desc_df[['entity','description_formatted']].apply(lambda x: multi_ref_entity_category_extractor(x.entity,x.description_formatted),axis=1)

Category Output:
container
Category Output:
process
Category Output:
application
Category Output:
process
Category Output:
application
Category Output:
application
Category Output:
process
Category Output:
container
Category Output:
directory
Category Output:
container
Category Output:
directory
Category Output:
container
Category Output:
file
Category Output:
container
Category Output:
container
Category Output:
network
Category Output:
process
Category Output:
application
Category Output:
application
Category Output:
application
Category Output:
software
Category Output:
application
Category Output:
application
Category Output:
application
Category Output:
application
Category Output:
container
Category Output:
header
Category Output:
process
Category Output:
container
Category Output:
process
Category Output:
container
Category Output:
container
Category Output:
process
Category Output:
process
Category Output:
network
Category Output:
container
Category Output:
DNS
Category Output:

Category Output:
storage
Category Output:
storage
Category Output:
container
Category Output:
container
Category Output:
process
Category Output:
container
Category Output:
application
Category Output:
application
Category Output:
software
Category Output:
application
Category Output:
application
Category Output:
persistent volume
Category Output:
process
Category Output:
process
Category Output:
software
Category Output:
process
Category Output:
container
Category Output:
container
Category Output:
metadata
Category Output:
software
Category Output:
software
Category Output:
application
Category Output:
application
Category Output:
application
Category Output:
software
Category Output:
container
Category Output:
software
Category Output:
application
Category Output:
application
Category Output:
container
Category could not be parsed due to corrupt format and doc
Category Output:
container
Category Output:
application
Category Output:
container
Category Output:
container
Category Outpu

Category Output:
process
Category Output:
path
Category Output:
application
Category Output:
container
Category Output:
storage
Category Output:
permissions
Category Output:
storage
Category Output:
database
Category Output:
container
Category Output:
process
Category Output:
container
Category Output:
container
Category could not be parsed due to corrupt format and doc
Category could not be parsed due to corrupt format and doc
Category Output:
container
Category Output:
container
Category Output:
container
Category Output:
container
Category Output:
application
Category Output:
container
Category Output:
container
Category Output:
container
Category Output:
container
Category Output:
container
Category Output:
container
Category Output:
application
Category Output:
container
Category Output:
container
Category Output:
container
Category Output:
container
Category Output:
container
Category Output:
container
Category Output:
container
Category Output:
network
Category Output:
container

In [24]:
import networkx as nx



graph_output_dir="./graph_output_networkx/"
input_graph="graph_phase2_with_single_entity_desc_embeddings.graphml"
G=nx.read_graphml(graph_output_dir+input_graph)


In [17]:
entity_multi_node_desc_df[['entity','description_formatted','category']].apply(lambda x: multi_ref_node_builder(x.entity,x.description_formatted,x.category),axis=1)

0      None
1      None
2      None
3      None
4      None
       ... 
742    None
743    None
744    None
745    None
746    None
Length: 747, dtype: object

In [18]:
pdf_enrichment_output_dir='../pdf_enrichment/pdf_enriched_output/'


import pickle
with open(pdf_enrichment_output_dir+pdf_enrichment_output_file, 'rb') as handle:
    document_dict_deserialized = pickle.load(handle)

multi_ref_entity_lst=list(entity_multi_node_desc_df['entity'])
#G=nx.read_graphml(graph_output_dir+input_graph)



G=link_multi_ref_entities_with_page(G,document_dict_deserialized)


Entity:
$ kubectl get po
Entity:
--all
Entity:
--all-namespaces
Entity:
--overwrite
Entity:
/api
Entity:
/apis
Entity:
/bin/sleep
Entity:
/etc/nginx/conf.d directory
Entity:
/logs/
Entity:
/usr/share/nginx/html
Entity:
/var/
Entity:
/var/htdocs
Entity:
/var/ready file
Entity:
/var/run/secrets/kubernetes.io/serviceaccount
Entity:
/var/run/secrets/kubernetes.io/serviceaccount/
Entity:
10.111.249.153
Entity:
AGE
Entity:
API
Entity:
API Server
Entity:
API object
Entity:
API objects
Entity:
API server
Entity:
API server URL
Entity:
Account Service
Entity:
Admission Control plugin
Entity:
Always
Entity:
Authorization header
Entity:
Autoscaler
Entity:
Backend pod
Entity:
BestEffort
Entity:
BuildConfig
Entity:
Burstable
Entity:
CAP_CHOWN
Entity:
CHOWN
Entity:
CIDR notation
Entity:
CMD
Entity:
CNAME record
Entity:
CNI plugin
Entity:
CONTAINER_CPU_REQUEST_MILLICORES
Entity:
CONTAINER_MEMORY_LIMIT_KIBIBYTES
Entity:
CPU
Entity:
CPU cores
Entity:
CPU requests
Entity:
CPU time
Entity:
CPU usage
Enti

Entity:
API server URL
Entity:
Account Service
Entity:
Admission Control plugin
Entity:
Always
Entity:
Authorization header
Entity:
Autoscaler
Entity:
Backend pod
Entity:
BestEffort
Entity:
BuildConfig
Entity:
Burstable
Entity:
CAP_CHOWN
Entity:
CHOWN
Entity:
CIDR notation
Entity:
CMD
Entity:
CNAME record
Entity:
CNI plugin
Entity:
CONTAINER_CPU_REQUEST_MILLICORES
Entity:
CONTAINER_MEMORY_LIMIT_KIBIBYTES
Entity:
CPU
Entity:
CPU cores
Entity:
CPU requests
Entity:
CPU time
Entity:
CPU usage
Entity:
CPU utilization
Entity:
CRD
Entity:
CRD (Custom Resource Definition)
Entity:
Client
Entity:
Cloud provider
Entity:
Cluster
Entity:
Cluster Autoscaler
Entity:
Cluster admin
Entity:
ClusterIP
Entity:
ClusterRole
Entity:
ClusterRoleBinding
Entity:
ClusterRoleBindings
Entity:
ClusterRoles
Entity:
ClusterServiceBroker
Entity:
ClusterServiceClass
Entity:
ConfigMap
Entity:
ConfigMap entries
Entity:
ConfigMap volume
Entity:
ConfigMaps
Entity:
Container
Entity:
Container image
Entity:
Container(s)
Enti

cluster
Entity:
cluster IP
Entity:
cluster nodes
Entity:
cluster-admin
Entity:
clusterIP
Entity:
clusterrolebinding
Entity:
clusterrolebindings
Entity:
clusterroles
Entity:
command
Entity:
command-line arguments
Entity:
configMap
Entity:
configMapKeyRef
Entity:
configmaps
Entity:
connection refused
Entity:
container
Entity:
container image
Entity:
container runtime
Entity:
container spec
Entity:
containerCpuRequestMilliCores
Entity:
containerCreating
Entity:
containerMemoryLimitBytes
Entity:
containerPort
Entity:
containers
Entity:
controller
Entity:
controllers
Entity:
cpu
Entity:
create
Entity:
create namespace
Entity:
creation_method
Entity:
curl
Entity:
curl command
Entity:
curl loop
Entity:
curl pod
Entity:
custom-namespace
Entity:
data
Entity:
database
Entity:
date
Entity:
dd
Entity:
debug
Entity:
default
Entity:
default ServiceAccount
Entity:
default namespace
Entity:
default-token
Entity:
default-token Secret
Entity:
defaultMode
Entity:
defaultRequest
Entity:
delete
Entity:
dep

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [21]:
nx.write_graphml_lxml(G, graph_output_dir+output_graph_graphml)
nx.write_gml(G, graph_output_dir+output_graph_gml)

In [25]:
def chroma_collection_populator(collection_name,docs_lst):
    idx=0
    for item in docs_lst:
        print('Item:')
        print(item)
        print('index:')
        print(idx)
        response = ollama.embeddings(model="mxbai-embed-large", prompt=item)
        embedding = response["embedding"]
        #print(np.array(embedding))
    
        collection_name.add(
            ids=[str(idx)],
            embeddings=[embedding],
            documents=[item]
            )
    
    
        idx=idx+1
        
    return collection_name

def query_collection(collection_name,query,n):
    query = query
    # generate an embedding for the prompt and retrieve the most relevant doc
    response = ollama.embeddings(
      prompt=query,
      model="mxbai-embed-large"
    )
    results = collection_name.query(
      query_embeddings=[response["embedding"]],
      n_results=n
    )
    return results

In [26]:
collection_entity = client.delete_collection(name="entities_entity")
collection_entity = client.get_or_create_collection(name="entities_entity")
docs_lst=list(set(list(entity_multi_node_desc_df['entity'])))
collection_entity=chroma_collection_populator(collection_entity,docs_lst)

Item:
azureDisk
index:
0
Item:
iptables rules
index:
1
Item:
JSON
index:
2
Item:
container
index:
3
Item:
OOMKilled
index:
4
Item:
replica
index:
5
Item:
list
index:
6
Item:
ClusterIP
index:
7
Item:
Volume
index:
8
Item:
maxUnavailable
index:
9
Item:
RWO,ROX
index:
10
Item:
my-nginx-config.conf
index:
11
Item:
RoleBindings
index:
12
Item:
selector
index:
13
Item:
Label selector
index:
14
Item:
provisioner
index:
15
Item:
Deployment controller
index:
16
Item:
kubia-manual.yaml
index:
17
Item:
localhost:8001
index:
18
Item:
Kubernetes cluster
index:
19
Item:
READY
index:
20
Item:
terminationMessagePath
index:
21
Item:
weight
index:
22
Item:
configMapKeyRef
index:
23
Item:
host
index:
24
Item:
rolling-update
index:
25
Item:
response.writeHead
index:
26
Item:
Services
index:
27
Item:
termination grace period
index:
28
Item:
apiGroups
index:
29
Item:
kubernetes Service
index:
30
Item:
IPC namespace
index:
31
Item:
Scheduler
index:
32
Item:
ReplicationController kubia-v2
index:
33
Item:
Kube

Item:
process
index:
281
Item:
node failure
index:
282
Item:
/var/run/secrets/kubernetes.io/serviceaccount
index:
283
Item:
pod
index:
284
Item:
NamespaceLifecycle
index:
285
Item:
hosts
index:
286
Item:
Retain
index:
287
Item:
port-forward
index:
288
Item:
Pod instance
index:
289
Item:
kubectl edit command
index:
290
Item:
kubectl get po
index:
291
Item:
kubectl exec
index:
292
Item:
CIDR notation
index:
293
Item:
GET request
index:
294
Item:
Product Catalog
index:
295
Item:
IP address
index:
296
Item:
volumes
index:
297
Item:
labelSelector
index:
298
Item:
Service resource
index:
299
Item:
revision
index:
300
Item:
lifecycle
index:
301
Item:
AGE
index:
302
Item:
annotations
index:
303
Item:
pod A
index:
304
Item:
node-type
index:
305
Item:
nslookup
index:
306
Item:
requests.cpu
index:
307
Item:
name
index:
308
Item:
Replicas
index:
309
Item:
serviceName
index:
310
Item:
ClusterRoleBinding
index:
311
Item:
availability-zone
index:
312
Item:
get
index:
313
Item:
service account
index:


Item:
latest
index:
561
Item:
Role
index:
562
Item:
CPU cores
index:
563
Item:
CNAME record
index:
564
Item:
mydockerhubsecret
index:
565
Item:
Memory
index:
566
Item:
operator
index:
567
Item:
default-token
index:
568
Item:
kubectl set image
index:
569
Item:
debug
index:
570
Item:
securityContext
index:
571
Item:
pod anti-affinity
index:
572
Item:
Job resource
index:
573
Item:
SIGTERM
index:
574
Item:
Pod A
index:
575
Item:
metrics
index:
576
Item:
main
index:
577
Item:
CronJob resource
index:
578
Item:
security context
index:
579
Item:
DaemonSets
index:
580
Item:
RESTARTS
index:
581
Item:
kubia-zxzij
index:
582
Item:
ls
index:
583
Item:
Namespace controller
index:
584
Item:
fortuneloop.sh
index:
585
Item:
schedule
index:
586
Item:
os.hostname()
index:
587
Item:
ReplicationController:v1
index:
588
Item:
ServiceInstance
index:
589
Item:
container spec
index:
590
Item:
readiness probe
index:
591
Item:
Deployment
index:
592
Item:
cpu
index:
593
Item:
glusterfs
index:
594
Item:
pod manife

In [27]:
query_collection(collection_entity,"tell me something about docker hub",3)

{'ids': [['537', '538', '526']],
 'distances': [[49.19931411743164, 133.4887237548828, 179.38531494140625]],
 'metadatas': [[None, None, None]],
 'embeddings': None,
 'documents': [['Docker Hub', 'Docker', 'docker0']],
 'uris': None,
 'data': None}

In [28]:
collection_desc = client.delete_collection(name="entities_db_desc")
collection_desc = client.get_or_create_collection(name="entities_db_desc")
docs_lst=list(set(list(entity_multi_node_desc_df['description_formatted'])))
collection_desc_data=chroma_collection_populator(collection_desc,docs_lst)

Item:
In a Kubernetes deployment, the second node refers to the secondary server or machine within the cluster that is responsible for hosting and managing containerized applications, alongside the primary node. This particular node, with an IP address of 130.211.99.206, serves as one of the critical components in the distributed system, ensuring high availability and scalability by sharing the workload with other nodes in the cluster.
index:
0
Item:
A cutting-edge, open-source analytics and visualization suite specifically designed to unlock the full potential of InfluxDB data. This innovative platform empowers users to gain deeper insights into their metrics by providing a comprehensive and interactive visualization experience. By leveraging advanced analytics capabilities, users can monitor and analyze their data with unparalleled precision, making informed decisions with confidence.
index:
1
Item:
Kubernetes is a container orchestration system that allows users to run a single-node

Item:
The `kubectl delete` command is used to remove Kubernetes resources such as ReplicationControllers, Pods, and other cluster entities. It can be executed with various options like `--cascade=false` to prevent cascading deletions, specifying the termination grace period for pods, or forcing deletion of a resource. This command is essential for maintaining a clean and organized Kubernetes cluster by removing unnecessary resources.
index:
20
Item:
A unique identifier for the Service Account that will authenticate and authorize a pod's access to cluster resources, ensuring secure and controlled interactions within the Kubernetes environment.
index:
21
Item:
A cryptographic file containing an encryption key, utilized for decrypting data previously encrypted using its paired public key. This key serves as a confidential access point, enabling authorized parties to retrieve and interpret sensitive information that was secured with the corresponding public key.
index:
22
Item:
In Kubernet

Item:
A Dockerfile, also known as a container specification or container definition, is a text file that contains instructions for building an image of a container. It defines the container's configuration, settings, and resource requirements, such as CPU and memory allocations, network interfaces, and storage volumes. The Dockerfile serves as a blueprint for creating a consistent and reproducible environment for running applications within containers. By specifying the base image, dependencies, and configurations, the Dockerfile enables developers to package their code and dependencies into a single, self-contained unit that can be easily deployed and managed across different environments.
index:
40
Item:
The primary host within a Kubernetes deployment, identified by its unique IP address (130.211.97.55), serving as the initial point of contact for the cluster's infrastructure and facilitating the orchestration of containerized applications across multiple nodes.
index:
41
Item:
A net

Item:
In a containerized system, Pods serve as the fundamental execution units. In Kubernetes, a Pod object represents this concept. The term 'pod' is often used in shortened form within kubectl commands. A pod resource in Kubernetes embodies this idea, and the name of the kube-proxy pod exemplifies its usage. Furthermore, 'pod' is utilized as a shorthand for pods, and it signifies the resource type for pods in Kubernetes. Lastly, the output format for the get command displays detailed information about pods.
index:
57
Item:
A file that stores the CPU request for a container, quantified in terms of milli-cores. This measurement represents the minimum amount of processing power required by the container to operate efficiently, allowing for optimal resource allocation and utilization within a Kubernetes cluster.
index:
58
Item:
In Kubernetes, you can use a tool like `curl` or a dedicated HTTP client library to send HTTP requests from within a pod. This can be achieved by running a separa

Item:
A Kubernetes ClusterRole that enables access to Persistent Volumes, allowing users to manage and interact with persistent storage resources within a cluster.
index:
75
Item:
Node.js is a cross-platform, open-source JavaScript runtime environment that allows developers to create scalable, high-performance server-side applications.
index:
76
Item:
A command-line interface (CLI) utility that enables users to interact with etcd, a distributed key-value store used in container orchestration and other applications. This tool provides a simple and intuitive way to manage etcd clusters, allowing users to perform various operations such as creating, updating, and deleting keys, as well as monitoring the health and status of the cluster.
index:
77
Item:
A Kubernetes object, referred to as a 'Pod', serves as the basic execution unit in a cluster. It represents a logical host for one or more application containers. To retrieve a list of all currently running Pods within a cluster, you can ut

...

Item:
The service responsible for providing access to Grafana within a Kubernetes environment is named and resides in the kube-system namespace, specifically exposing Grafana's graphical user interface through its web console.
index:
665
Item:
A Kubernetes Admission Controller plugin that validates pod creation based on predefined policies, ensuring compliance with desired standards and configurations.
index:
666
Item:
A metadata attribute, known as a label, that can be attached to a Kubernetes Pod. This label serves as a unique identifier and allows for tracking the origin or creation method of the pod, providing valuable context for management and maintenance purposes.
index:
667
Item:
Google Cloud Persistent Storage is a cloud-based, highly available, and scalable storage solution for Google Cloud Platform. It provides a network-attached storage (NAS) like experience in Google Kubernetes Engine, allowing users to store and manage large amounts of data. This persistent storage soluti

Item:
A TopologyKey is a configuration parameter that defines the scope for pod affinity, specifying the topology of a node or a group of nodes. It identifies the type of resources (e.g., CPU, memory, storage) that should be considered when scheduling pods. This key ensures that pods with specific affinities are deployed to nodes with matching topological characteristics, such as being on the same rack or having similar resource profiles. By using TopologyKey, administrators can fine-tune their cluster's resource allocation and placement strategies, making it easier to manage complex deployments and ensure efficient resource utilization.
index:
682
Item:
A key performance indicator (KPI) called CPU utilization is utilized by Kubernetes' horizontal pod autoscaler (HPA) to gauge the load on a system. This metric enables automatic scaling based on the number of replicas required to maintain optimal CPU usage within a specified threshold. The HPA calculates the desired replica count by mon

Item:
A Kubernetes label key, 'rack', allows administrators to categorize and manage nodes within a cluster based on their physical or logical location. This enables efficient resource allocation, monitoring, and maintenance by grouping nodes that share the same rack, facilitating easier management and scaling of applications.
index:
700
Item:
A Role is a collection of permissions that dictate which verbs can be executed on specific resources within a namespace. It allows access to resources within the same namespace and can include an authentication token with elevated privileges compared to those defined by a Cluster-Role. Roles are used to define what actions can be performed on which resources in a Kubernetes cluster, providing a granular level of control over permissions. They can be granted to users or groups, enabling fine-tuned access management within the cluster.
index:
701
Item:
This property, often denoted as 'maxSurge', is a crucial setting in Kubernetes deployments. It di

Item:
A regular Kubernetes service that can be accessed internally within the cluster via its assigned IP address, distinct from ExternalName services which are not assigned an IP address and are typically used for DNS-based routing.
index:
717
Item:
A liveness probe is a mechanism in Kubernetes that periodically checks whether a container is running correctly by executing a command or making an HTTP request. This ensures the container's health and restarts it if it fails, maintaining application availability and reliability.
index:
718
Item:
A resource-based metric used for scaling pods based on their consumption of resources such as CPU and memory. This type of metric allows Kubernetes to dynamically adjust the number of running pods in response to changes in system load, ensuring efficient utilization of available resources.
index:
719
Item:
A sophisticated traffic management system, known as a load balancer, efficiently disperses incoming client connections to multiple instances of

Item:
In Kubernetes, Resource Quotas (also known as Resource Limits) are constraints set by users on the maximum amount of resources a pod or container can consume. This includes limits for CPU and memory usage. These quotas help prevent resource overconsumption and ensure efficient utilization of cluster resources. The LimitRange resource definition specifies these limits for pods and containers, ensuring that they do not exceed the allocated resources. By setting Resource Quotas, users can control the maximum total limits for CPU and memory usage by a pod, thereby preventing potential resource bottlenecks and maintaining a stable Kubernetes environment.
index:
737
Item:
The cron schedule format is used to specify the timing of a job's execution, allowing it to run periodically or at a specific point in the future. This format is utilized within the CronJob specification to define when a job should be executed.
index:
738
Item:
In Kubernetes, you can utilize the `kubectl` command or m

In [29]:
query_collection(collection_desc_data,"data plane and control plane",3)

{'ids': [['480', '609', '526']],
 'distances': [[194.7187042236328, 196.69998168945312, 242.23260498046875]],
 'metadatas': [[None, None, None]],
 'embeddings': None,
 'documents': [["The Control Plane is a critical component in Kubernetes that oversees the state of the entire cluster, ensuring it remains in a desired condition. It manages the lifecycle of various controllers, such as ReplicaSets and Deployments, by observing changes to deployed resources and acting accordingly. This component runs multiple controllers simultaneously, including those responsible for managing Horizontal Pod Autoscaling and other control plane functions. The Control Plane is essentially a single pod that hosts each controller within it, providing a centralized management system for the cluster's state. As part of the Service Catalog system, it plays a vital role in maintaining the overall health and stability of the Kubernetes environment.",
   "A Kubernetes cluster's control plane, also known as the man

In [30]:
collection_cat = client.delete_collection(name="entities_db_cat")
collection_cat = client.get_or_create_collection(name="entities_db_cat")
docs_lst=list(set(list(entity_multi_node_desc_df['category'])))
collection_cat_data=chroma_collection_populator(collection_cat,docs_lst)

Item:
application
index:
0
Item:
node
index:
1
Item:
persistent volume
index:
2
Item:
label
index:
3
Item:
path
index:
4
Item:
software
index:
5
Item:
image
index:
6
Item:
container
index:
7
Item:
config
index:
8
Item:
port
index:
9
Item:
protocol
index:
10
Item:
load balancer
index:
11
Item:
cloud
index:
12
Item:
database
index:
13
Item:
fieldPath
index:
14
Item:
users
index:
15
Item:
capability
index:
16
Item:
resource management
index:
17
Item:
directory
index:
18
Item:
volume
index:
19
Item:
permissions
index:
20
Item:
storage
index:
21
Item:
selector
index:
22
Item:
revision
index:
23
Item:
metrics
index:
24
Item:
kubectl
index:
25
Item:
environment
index:
26
Item:
service
index:
27
Item:
resource
index:
28
Item:
memory
index:
29
Item:
file
index:
30
Item:
PersistentVolume
index:
31
Item:
filesystem
index:
32
Item:
Not Available
index:
33
Item:
Persistent Volume
index:
34
Item:
environment variable
index:
35
Item:
header
index:
36
Item:
hardware
index:
37
Item:
probe
index:
38
Ite

In [31]:
query_collection(collection_cat_data,"Replication Controller",3)

{'ids': [['11', '39', '10']],
 'distances': [[225.3902541546911, 252.49913846118858, 277.4212555808041]],
 'metadatas': [[None, None, None]],
 'embeddings': None,
 'documents': [['load balancer', 'load balancing', 'protocol']],
 'uris': None,
 'data': None}

In [32]:
####The main contents of Kubernets In Action book is contained from page 87 to 565####
####Thats why we will only take the sliced portion i.e. from page 87 to 565 of the pdf dictionary list#####
nt = Network('800px', '2000px',notebook=True,cdn_resources='remote')
# populates the nodes and edges data structures
nt.from_nx(G)
nt.toggle_physics(True)
nt.show('nx1.html')
#nt.show_buttons(filter_=['physics'])
#nt.save('nx2.html')
#nt.write_html('graph_stage1.html')

nx1.html
